In [ ]:

# To be installed:
# Flask==0.12.2: pip install Flask==0.12.2
# Postman HTTP Client: https://www.getpostman.com/
# requests==2.18.4: pip install requests==2.18.4

# Importing the libraries
import json
from flask import Flask, jsonify, request
import requests
from uuid import uuid4
from urllib.parse import urlparse
import os
import pandas as pd 
import numpy as np 

from keras.models import load_model
import cv2
import numpy as np
import os
from matplotlib import pyplot as plt
import time
import imutils
import mediapipe as mp




mp_holistic = mp.solutions.holistic # Holistic model
mp_drawing = mp.solutions.drawing_utils # Drawing utilities
mp_hands = mp.solutions.hands
modelpsl = load_model('action.h5')
modelAtOZ = load_model('actionAtoz.h5')
actions = np.array(['Accept', 'Appear', 'Argentina', 'Away', 'Barbecue', 'Bathe', 'Birthday', 'Bitter', 'Born', 'Breakfast', 'Bright', 'Buy', 'Call', 'Candy', 'Catch', 'Chewing-gum', 'Coins', 'Copy', 'Country', 'Dance', 'Deaf', 'Drawer', 'Enemy', 'Find', 'Food', 'Give', 'Green', 'Help', 'Hungry', 'Last name', 'Learn', 'Light-blue', 'Man', 'Map', 'Milk', 'Mock', 'Music', 'None', 'Opaque', 'Patience', 'Perfume','Photo', 'Realize', 'Red', 'Red2', 'Rice', 'Run', 'Ship', 'Shut down', 'Skimmer', 'Son', 'Spaghetti', 'Sweet milk', 'Thanks', 'To land', 'Trap', 'Uruguay', 'Water', 'Where', 'Women', 'Yellow', 'Yogurt'])
actions2 = np.array(['A','B', 'C','D','E','F', 'G','H','I', 'K','L','M', 'N', 'O','P','Q','R','S', 'T', 'U','V', 'W', 'X', 'Z'])
def mediapipe_detection(image, model):
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB) # COLOR CONVERSION BGR 2 RGB
    image.flags.writeable = False                  # Image is no longer writeable
    results = model.process(image)                 # Make prediction
    image.flags.writeable = True                   # Image is now writeable 
    image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR) # COLOR COVERSION RGB 2 BGR
    return image, results

def draw_landmarks2(image, results):
    #mp_drawing.draw_landmarks(image, results.face_landmarks, mp_holistic.FACE_CONNECTIONS) # Draw face connections
    #mp_drawing.draw_landmarks(image, results.pose_landmarks, mp_holistic.POSE_CONNECTIONS) # Draw pose connections
  
            for num, hand in enumerate(results.multi_hand_landmarks):
                mp_drawing.draw_landmarks(image, hand, mp_hands.HAND_CONNECTIONS, 
                                        mp_drawing.DrawingSpec(color=(121, 22, 76), thickness=2, circle_radius=4),
                                        mp_drawing.DrawingSpec(color=(250, 44, 250), thickness=2, circle_radius=2),
                                         )

def draw_landmarks(image, results):
    mp_drawing.draw_landmarks(image, results.face_landmarks, mp_holistic.FACE_CONNECTIONS) # Draw face connections
    mp_drawing.draw_landmarks(image, results.pose_landmarks, mp_holistic.POSE_CONNECTIONS) # Draw pose connections
    mp_drawing.draw_landmarks(image, results.left_hand_landmarks, mp_holistic.HAND_CONNECTIONS) # Draw left hand connections
    mp_drawing.draw_landmarks(image, results.right_hand_landmarks, mp_holistic.HAND_CONNECTIONS) # Draw right hand connections
    



def draw_styled_landmarks(image, results):
    # Draw face connections
    mp_drawing.draw_landmarks(image, results.face_landmarks, mp_holistic.FACE_CONNECTIONS, 
                             mp_drawing.DrawingSpec(color=(80,110,10), thickness=1, circle_radius=1), 
                             mp_drawing.DrawingSpec(color=(80,256,121), thickness=1, circle_radius=1)
                             ) 
    # Draw pose connections
    mp_drawing.draw_landmarks(image, results.pose_landmarks, mp_holistic.POSE_CONNECTIONS,
                             mp_drawing.DrawingSpec(color=(80,22,10), thickness=2, circle_radius=4), 
                             mp_drawing.DrawingSpec(color=(80,44,121), thickness=2, circle_radius=2)
                             ) 
    # Draw left hand connections
    mp_drawing.draw_landmarks(image, results.left_hand_landmarks, mp_holistic.HAND_CONNECTIONS, 
                             mp_drawing.DrawingSpec(color=(121,22,76), thickness=2, circle_radius=4), 
                             mp_drawing.DrawingSpec(color=(121,44,250), thickness=2, circle_radius=2)
                             ) 
    # Draw right hand connections  
    mp_drawing.draw_landmarks(image, results.right_hand_landmarks, mp_holistic.HAND_CONNECTIONS, 
                             mp_drawing.DrawingSpec(color=(245,117,66), thickness=2, circle_radius=4), 
                             mp_drawing.DrawingSpec(color=(245,66,230), thickness=2, circle_radius=2)
                             ) 
    
def draw_styled_landmarks2(image, results):
    # Draw face connections
   # mp_drawing.draw_landmarks(image, results.face_landmarks, mp_holistic.FACE_CONNECTIONS, 
                             #mp_drawing.DrawingSpec(color=(80,110,10), thickness=1, circle_radius=1), 
                             #mp_drawing.DrawingSpec(color=(80,256,121), thickness=1, circle_radius=1)
                             #) 
    # Draw pose connections
    #mp_drawing.draw_landmarks(image, results.pose_landmarks, mp_holistic.POSE_CONNECTIONS,
                             #mp_drawing.DrawingSpec(color=(80,22,10), thickness=2, circle_radius=4), 
                             #mp_drawing.DrawingSpec(color=(80,44,121), thickness=2, circle_radius=2)
                           #  ) 
    # Draw left hand connections
       if results.multi_hand_landmarks:
            for num, hand in enumerate(results.multi_hand_landmarks):
                mp_drawing.draw_landmarks(image, hand, mp_hands.HAND_CONNECTIONS, 
                                        mp_drawing.DrawingSpec(color=(121, 22, 76), thickness=2, circle_radius=4),
                                        mp_drawing.DrawingSpec(color=(250, 44, 250), thickness=2, circle_radius=2),
                                         )
    # Draw right hand connections  
    #mp_drawing.draw_landmarks(image, results.right_hand_landmarks, mp_holistic.HAND_CONNECTIONS, 
                             #mp_drawing.DrawingSpec(color=(245,117,66), thickness=2, circle_radius=4), 
                             #mp_drawing.DrawingSpec(color=(245,66,230), thickness=2, circle_radius=2)
                            # )     
    

def extract_keypoints(results):
    pose = np.array([[res.x, res.y, res.z, res.visibility] for res in results.pose_landmarks.landmark]).flatten() if results.pose_landmarks else np.zeros(33*4)
    face = np.array([[res.x, res.y, res.z] for res in results.face_landmarks.landmark]).flatten() if results.face_landmarks else np.zeros(468*3)
    lh = np.array([[res.x, res.y, res.z] for res in results.left_hand_landmarks.landmark]).flatten() if results.left_hand_landmarks else np.zeros(21*3)
    rh = np.array([[res.x, res.y, res.z] for res in results.right_hand_landmarks.landmark]).flatten() if results.right_hand_landmarks else np.zeros(21*3)
    return np.concatenate([pose, lh, rh])


def extract_keypoints2(results):
    hand = np.array([[[res.x, res.y, res.z] for res in rest.landmark]for rest in results.multi_hand_landmarks]).flatten() if results.multi_hand_landmarks else np.zeros(21*3);
    return hand
    
def ValuePredictor(path):
    sequence = []
    sentence = []
    predictions = []
    threshold = 0.8
    print(path)
    cap = cv2.VideoCapture(str(path))
    with mp_holistic.Holistic(min_detection_confidence=0.5, min_tracking_confidence=0.5) as holistic: 
        sequence = []
        for seq in range(5):
            # Loop through video length aka sequence length
            for frame_num in range(20):

                # Read feed
                ret, frame = cap.read()
                if ret==True:
                # Make detections
                    frame= imutils.resize(frame, width=920, height=920)
                    image, results = mediapipe_detection(frame, holistic)
                    #print(image)

                    # Draw landmarks
                    draw_styled_landmarks(image, results)

                    # NEW Apply wait logic
                    if frame_num == 0: 
                        cv2.rectangle(image, (0,0), (640, 40), (245, 117, 16), -1)
                        cv2.putText(image, 'Collecting frames for {}'.format(seq), (25,32), 
                                                           cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 1, cv2.LINE_AA)

                    # Show to screenq
                        cv2.imshow('OpenCV Feed', image)
                        #cv2.waitKey(1000)
                    else: 
                        cv2.putText(image, 'Collecting frames for {}'.format(seq), (25,32),cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 1, cv2.LINE_AA)
                        # Show to screen
                        cv2.imshow('OpenCV Feed', image)

                    # NEW Export keypoints
                    #print(results.multi_hand_landmarks)
                    keypoints = extract_keypoints(results)
                    print(keypoints)
                    npy_path = os.path.join('test', str(seq))
                    np.save(npy_path, keypoints)

                    # Break gracefully
                    if cv2.waitKey(15) & 0xFF == ord('q'):
                        break

    cap.release()
    cv2.destroyAllWindows()
    for frame_num in range(5):
        res = np.load(os.path.join('test', "{}.npy".format(frame_num)))
        #print(np.array(res).size)
        sequence.append(res)
        print(res)
        #print(window)

    #print(sequences)

    res = modelpsl.predict(np.expand_dims(sequence, axis=0))[0]
    print(actions[np.argmax(res)])
    predictions.append(np.argmax(res))
    return actions[np.argmax(res)]




def ValuePredictor2(path):
    sequence = []
    sentence = []
    predictions = []
    threshold = 0.8
    #print('hellooo')
    #print(path)
    cap = cv2.VideoCapture(str(path))
    #print(cap)
    with mp_hands.Hands( max_num_hands=1,min_detection_confidence=0.5, min_tracking_confidence=0.5) as hands: 
        sequence = []
        for seq in range(3):
            # Loop through video length aka sequence length
            for frame_num in range(30):

                # Read feed
                ret, frame = cap.read()
                
                #print(frame)
                if ret==True:
                # Make detections
                    frame= imutils.resize(frame, width=520, height=420)
                    image, results = mediapipe_detection(frame, hands)
                    #print(image)

                    # Draw landmarks
                    draw_styled_landmarks2(image, results)

                    # NEW Apply wait logic
                    if frame_num == 0: 
                        cv2.rectangle(image, (0,0), (640, 40), (245, 117, 16), -1)
                        cv2.putText(image, 'Collecting frames for {}'.format(seq), (25,32), 
                                                           cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 1, cv2.LINE_AA)

                    # Show to screenq
                        cv2.imshow('OpenCV Feed', image)
                        #cv2.waitKey(1000)
                    else: 
                        cv2.putText(image, 'Collecting frames for {}'.format(seq), (25,32),cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 1, cv2.LINE_AA)
                        # Show to screen
                        cv2.imshow('OpenCV Feed', image)

                    # NEW Export keypoints
                    #print(results.multi_hand_landmarks)
                    keypoints = extract_keypoints2(results)
                    print(keypoints)
                    npy_path = os.path.join('testAtoz', str(seq))
                    np.save(npy_path, keypoints)

                    # Break gracefully
                    if cv2.waitKey(15) & 0xFF == ord('q'):
                        break

    cap.release()
    cv2.destroyAllWindows()
    for frame_num in range(3):
        res = np.load(os.path.join('testAtoz', "{}.npy".format(frame_num)))
        #print(np.array(res).size)
        sequence.append(res)
        #print(window)

    #print(sequences)

    res = modelAtOZ.predict(np.expand_dims(sequence, axis=0))[0]
    print(actions2[np.argmax(res)])
    predictions.append(np.argmax(res))
    return actions2[np.argmax(res)]


# Creating a Web App
app = Flask(__name__)

# Creating an address for the node on Port 5000
node_address = str(uuid4()).replace('-', '')




# Adding a new transaction to the Blockchain
@app.route('/predict', methods = ['POST'])
def upload():
    if "video" in request.files:
        videofile = request.files["video"]
        videofile.save(videofile.filename)
        print(videofile)
        return jsonify(ValuePredictor(videofile.filename)), 201
    
# Adding a new transaction to the Blockchain
@app.route('/Atoz', methods = ['POST'])
def upload3():
    if "video" in request.files:
        videofile = request.files["video"]
        videofile.save(videofile.filename)
        print(videofile)
        return jsonify(ValuePredictor2(videofile.filename)), 201
      

@app.route('/', methods = ['GET'])
def upload2():
    
    return jsonify('Hello'), 201



# Running the app
app.run(host = 'localhost', port = 5000)

 * Serving Flask app "__main__" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


 * Running on http://localhost:5000/ (Press CTRL+C to quit)


<FileStorage: '050_001_001.mp4' ('video/mp4')>
050_001_001.mp4
[ 4.69759732e-01  2.69202828e-01 -6.89695597e-01  9.99669075e-01
  4.84315902e-01  2.31191397e-01 -6.45081699e-01  9.99425292e-01
  4.94879603e-01  2.33281136e-01 -6.45378828e-01  9.99406099e-01
  5.03984869e-01  2.36007035e-01 -6.45678163e-01  9.99354064e-01
  4.56511647e-01  2.29748726e-01 -6.44966364e-01  9.99384642e-01
  4.46734726e-01  2.30358303e-01 -6.45181656e-01  9.99417067e-01
  4.37289536e-01  2.31071889e-01 -6.45375311e-01  9.99405861e-01
  5.19701183e-01  2.65913904e-01 -3.62119794e-01  9.99335825e-01
  4.28138047e-01  2.61162281e-01 -3.59076113e-01  9.99442756e-01
  4.90094185e-01  3.16996098e-01 -5.82800031e-01  9.99795258e-01
  4.53595400e-01  3.15479159e-01 -5.81446230e-01  9.99805391e-01
  5.89980006e-01  5.34131050e-01 -1.99549139e-01  9.99691963e-01
  3.65051299e-01  5.38199723e-01 -1.57041132e-01  9.99638438e-01
  6.28957570e-01  8.49425495e-01 -3.13338876e-01  9.42860603e-01
  3.30148041e-01  8.3539050

[ 4.70426351e-01  2.68599927e-01 -6.38028681e-01  9.99690652e-01
  4.84931380e-01  2.31093884e-01 -5.93890131e-01  9.99468088e-01
  4.95325416e-01  2.32882395e-01 -5.94208419e-01  9.99454260e-01
  5.04124463e-01  2.35125050e-01 -5.94502509e-01  9.99404490e-01
  4.57454771e-01  2.29743928e-01 -5.94428778e-01  9.99431908e-01
  4.47637498e-01  2.30329350e-01 -5.94674230e-01  9.99464869e-01
  4.38234836e-01  2.31124118e-01 -5.94897211e-01  9.99449551e-01
  5.19008756e-01  2.62326390e-01 -3.21468860e-01  9.99403894e-01
  4.28602427e-01  2.61372477e-01 -3.21946025e-01  9.99492168e-01
  4.90110010e-01  3.16362888e-01 -5.36708593e-01  9.99817669e-01
  4.53928560e-01  3.15435052e-01 -5.36272764e-01  9.99824762e-01
  5.89178979e-01  5.33378601e-01 -1.76007688e-01  9.99727428e-01
  3.65092754e-01  5.37919819e-01 -1.40316024e-01  9.99647141e-01
  6.28834069e-01  8.47867548e-01 -2.91810781e-01  9.48809385e-01
  3.30075890e-01  8.37595284e-01 -2.27347046e-01  8.90039682e-01
  5.51343918e-01  9.11377

[ 0.47044104  0.26775768 -0.65183312  0.99970913  0.48503762  0.23077057
 -0.60758185  0.99949908  0.49536738  0.23232685 -0.60789251  0.9994899
  0.50414038  0.23433791 -0.60818946  0.99944168  0.45764014  0.22952653
 -0.60781825  0.99946362  0.44785249  0.23004079 -0.60805357  0.99949688
  0.43854553  0.23093756 -0.6082648   0.99947703  0.51852471  0.26078191
 -0.33134389  0.99945271  0.42886025  0.26127601 -0.33020741  0.99952382
  0.48982143  0.31534421 -0.54836369  0.9998349   0.45393285  0.31480297
 -0.54759574  0.99983943  0.58912373  0.53350466 -0.17996055  0.99975407
  0.3651801   0.53788871 -0.14190014  0.9996593   0.62870729  0.84771425
 -0.29895541  0.95369506  0.33006933  0.83699328 -0.22363405  0.89855129
  0.55157542  0.91079235 -0.72902423  0.72656184  0.34357801  0.92185599
 -0.67380178  0.54206842  0.52738881  0.93761772 -0.83750117  0.57777679
  0.34397569  0.9564358  -0.77559829  0.4510622   0.52320015  0.90024334
 -0.84925473  0.60889757  0.35095394  0.92860508 -0.

...

[ 4.90110040e-01  2.71769255e-01 -6.67929828e-01  9.99746561e-01
  5.02321899e-01  2.33784556e-01 -6.22877419e-01  9.99568880e-01
  5.10069549e-01  2.35348448e-01 -6.23189509e-01  9.99534607e-01
  5.17804921e-01  2.36370847e-01 -6.23386025e-01  9.99502659e-01
  4.73583907e-01  2.30767339e-01 -6.24085426e-01  9.99588966e-01
  4.63745952e-01  2.30784923e-01 -6.24299526e-01  9.99619365e-01
  4.53679681e-01  2.31097028e-01 -6.24496043e-01  9.99649346e-01
  5.27378261e-01  2.60071576e-01 -3.44882756e-01  9.99588311e-01
  4.39957649e-01  2.59891987e-01 -3.50338608e-01  9.99752760e-01
  5.05658209e-01  3.18913966e-01 -5.65813482e-01  9.99918520e-01
  4.70047683e-01  3.18625927e-01 -5.66552877e-01  9.99926925e-01
  5.88042438e-01  5.32207727e-01 -1.86981663e-01  9.99867618e-01
  3.67987037e-01  5.19218683e-01 -1.85092777e-01  9.99887824e-01
  6.30021513e-01  8.75690401e-01 -3.17633748e-01  9.69793260e-01
  3.02605808e-01  8.47746372e-01 -2.64689028e-01  9.84848559e-01
  5.35793662e-01  8.76543

[ 4.90128785e-01  2.71935195e-01 -6.64405465e-01  9.99748290e-01
  5.02359629e-01  2.33932629e-01 -6.19148850e-01  9.99566257e-01
  5.10119021e-01  2.35496938e-01 -6.19473338e-01  9.99529600e-01
  5.17843544e-01  2.36496314e-01 -6.19693875e-01  9.99501884e-01
  4.73641813e-01  2.30966464e-01 -6.20873630e-01  9.99589086e-01
  4.63787705e-01  2.31045574e-01 -6.21084034e-01  9.99617100e-01
  4.53704864e-01  2.31409803e-01 -6.21271908e-01  9.99651849e-01
  5.27486324e-01  2.60095716e-01 -3.41406882e-01  9.99582827e-01
  4.39978570e-01  2.60107845e-01 -3.46875221e-01  9.99759614e-01
  5.05701542e-01  3.19030344e-01 -5.62112868e-01  9.99920607e-01
  4.70104516e-01  3.18987817e-01 -5.63552201e-01  9.99929965e-01
  5.88057637e-01  5.32187700e-01 -1.83707699e-01  9.99870300e-01
  3.67916614e-01  5.19060910e-01 -1.81028575e-01  9.99897301e-01
  6.28940940e-01  8.76653433e-01 -3.12725306e-01  9.67937410e-01
  3.01860094e-01  8.50841761e-01 -2.36312851e-01  9.85213518e-01
  5.28552055e-01  8.75296

[ 4.90012348e-01  2.71823764e-01 -6.37413621e-01  9.99742448e-01
  5.02239227e-01  2.33919159e-01 -5.94268382e-01  9.99551415e-01
  5.10095358e-01  2.35469162e-01 -5.94565034e-01  9.99510467e-01
  5.17760694e-01  2.36450240e-01 -5.94748616e-01  9.99488115e-01
  4.73577231e-01  2.30996042e-01 -5.95141709e-01  9.99577522e-01
  4.63716120e-01  2.31108174e-01 -5.95320225e-01  9.99603152e-01
  4.53619540e-01  2.31512338e-01 -5.95509052e-01  9.99644995e-01
  5.27506113e-01  2.60019064e-01 -3.26675177e-01  9.99566257e-01
  4.39989805e-01  2.60246366e-01 -3.29716563e-01  9.99759972e-01
  5.05683362e-01  3.18755239e-01 -5.39151788e-01  9.99920785e-01
  4.70072806e-01  3.18916440e-01 -5.39500058e-01  9.99931276e-01
  5.88054001e-01  5.32170236e-01 -1.78973213e-01  9.99871016e-01
  3.67882758e-01  5.18690586e-01 -1.66526675e-01  9.99905229e-01
  6.27062023e-01  8.77898037e-01 -2.86576688e-01  9.66433704e-01
  3.00324887e-01  8.51283908e-01 -1.95080653e-01  9.85749006e-01
  5.14028013e-01  8.70011

127.0.0.1 - - [02/Oct/2023 17:14:27] "POST /predict HTTP/1.1" 201 -


Accept
